In [5]:
#HyprParams
inputdim = 10

In [4]:
#Sequential 모델은 레이어를 선형적으로 쌓는다.
from numpy import array
from keras  import Sequential
from keras.layers import Dense, Activation, LSTM

x = array([[1,2,3], [2,3,4], [3,4,5], [4,5,6], [5,6,7], [6,7,8], [7,8,9] , [8,9,10], [9,10,11], [10,11,12], [20,30,40], [40,50,60]])
y = array([4,5,6,7,8,9,10,11,12,13, 50, 70])


In [6]:
print(x.shape)
print(y.shape)

(12, 3)
(12,)


In [7]:
x = x.reshape((x.shape[0], x.shape[1], 1))

In [8]:
print(x.shape)

(12, 3, 1)


In [9]:
model = Sequential()
model.add(LSTM(20, activation = 'relu', input_shape=(3,1)))
model.add(Dense(5))
model.add(Dense(1))
model.compile(optimizer='adam', loss='mse')

from keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(monitor='loss', patience=10, mode='auto')
model.fit(x, y, epochs=1000, batch_size=1, verbose=2, callbacks=[early_stopping])
x_input = array([25,35,45])
x_input = x_input.reshape((1,3,1))

yhat = model.predict(x_input)
print(yhat)

Epoch 1/1000
 - 1s - loss: 750.5427
Epoch 2/1000
 - 0s - loss: 732.5768
Epoch 3/1000
 - 0s - loss: 711.7232
Epoch 4/1000
 - 0s - loss: 694.9550
Epoch 5/1000
 - 0s - loss: 671.0088
Epoch 6/1000
 - 0s - loss: 643.7903
Epoch 7/1000
 - 0s - loss: 605.9007
Epoch 8/1000
 - 0s - loss: 513.4071
Epoch 9/1000
 - 0s - loss: 270.1301
Epoch 10/1000
 - 0s - loss: 94.4189
Epoch 11/1000
 - 0s - loss: 52.3048
Epoch 12/1000
 - 0s - loss: 14.8138
Epoch 13/1000
 - 0s - loss: 7.7636
Epoch 14/1000
 - 0s - loss: 7.9816
Epoch 15/1000
 - 0s - loss: 7.1245
Epoch 16/1000
 - 0s - loss: 6.3708
Epoch 17/1000
 - 0s - loss: 5.7815
Epoch 18/1000
 - 0s - loss: 5.9203
Epoch 19/1000
 - 0s - loss: 5.4516
Epoch 20/1000
 - 0s - loss: 5.3052
Epoch 21/1000
 - 0s - loss: 5.3201
Epoch 22/1000
 - 0s - loss: 5.3967
Epoch 23/1000
 - 0s - loss: 5.1204
Epoch 24/1000
 - 0s - loss: 4.5354
Epoch 25/1000
 - 0s - loss: 4.6592
Epoch 26/1000
 - 0s - loss: 4.4346
Epoch 27/1000
 - 0s - loss: 4.3817
Epoch 28/1000
 - 0s - loss: 4.2866
Epoch 29

In [11]:
model.save('./model.h5')

In [13]:
from keras.models import load_model
model1 = load_model('./model.h5')

In [14]:
model1.predict(x_input)

array([[56.490707]], dtype=float32)

In [ ]:
#윤하씨 코드
import os
import locale
import pandas as pd
from datetime import datetime, timedelta
#from Creon_StockChart import MarketCap
locale.setlocale(locale.LC_ALL, 'ko_KR.UTF-8')

class Preprocess:

    def __init__(self):
        self.stockcode

    def __init__(self, stockcode):
        self.stockcode=stockcode
        self.date=0

    def SetStockCode(self, stockcode):
        self.stockcode=stockcode

    def GetStockCode(self):
        return self.stockcode

    def GetDate(self):
        return self.date

    def InitDataFrame(self):

        file=open(self.stockcode+".txt", "r")
        context=file.read().split("),") #)( 
        # tickData.txt 랑 새로 api 받은 텍스트 파일 다르게 바꿔야함, tickData-> ")," 새로 api -> )(

        time_list=[]
        price_list=[]
        state_list=[]
        amount_list=[]

        for i in range(0, len(context)):
            context[i]=context[i].strip("()").split(",")
            #if(len(context[i][1])<7):
            #   time=datetime.now().strftime("%Y%m%d")+context[i][1].strip()
            #else:
            #   time=context[i][1].strip()
            #종목코드 시간 현재체결가 체결상태 순간체결수량
            self.date=datetime.now().strftime("%Y%m%d")
            time_list.append(self.date+context[i][1].strip())
            price_list.append(int(context[i][4].strip())) #2
            state_list.append(int(context[i][5].strip("\' "))) #3
            if int(context[i][8].strip()) <0 :
                continue
            amount_list.append(int(context[i][8].strip()))

        time_list=pd.to_datetime(time_list)
        df = pd.DataFrame({"Price":price_list, "State":state_list, "Amount":amount_list}, index=time_list)
        file.close()
        print(df)
        return df

    def Resample_Data(self, time_span):

        df=self.InitDataFrame()
        Minute_df = pd.DataFrame()
        Minute_df['Price'] = df.Price.resample(time_span).last()
        Minute_df['State2'] = df[df.State == 2].Amount.resample(time_span).sum()
        Minute_df['State1'] = df[df.State == 1].Amount.resample(time_span).sum()
        Minute_df['Difference'] = Minute_df.State2 - Minute_df.State1

        #mc = MarketCap(self.stockcode, self.date)

        #Minute_df['X'] = Minute_df.Difference*Minute_df.Price
        '''
        체결량 차이(Difference) * 체결가(Price) / 시가총액 추가해야함
        '''
        return  Minute_df

if __name__ =="__main__":
    path = "C:/Users/user/Documents/DART/SystemTrading"
    os.chdir(path)

    stockcode="tickData"

    StockProcess=Preprocess(stockcode)
    ret = StockProcess.Resample_Data('1T')

    #ret.index = ret.index+ timedelta(minutes=1)
    print(ret)


In [ ]:
#윤진씨 코드

import pandas as pd
import os
import datetime
import numpy as np

#new_lst=[] # 시간별 호가창의 상태가 저장된 리스트

rate_lst=[]
def func1(): #file 읽어와서 날짜와 체결가 데이터만 저장한 dataframe으로 변환
    in_file = None
    in_file=open("tickData.txt","r") #file open

    in_str=in_file.read() #file read
    lst=in_str.split(')') # split
    new_lst=[]
    for el in lst :
        new_lst.append(el.lstrip(', ('))
    new_lst=list(filter(None,new_lst))
    #########################################리스트에 생성##################3
    time_lst=[]
    price_lst=[]
    for el in new_lst:
        lst2=el.split(',')
        #time=datetime.datetime.strptime(lst2[1].lstrip(),'%H%M%S')
        time=lst2[1].lstrip()
        time=datetime.datetime.now().strftime("%Y%m%d")+time
        time_lst.append(time) #시간리스트에 추가
        price_lst.append(int(lst2[4])) #체결가 리스트에 추가

    in_file.close()
    # dataframe으로 변환 ('시간'열 과 '체결가' 열 2개의 열로 이루어진 dataframe)
    time_lst=pd.to_datetime(time_lst)
    raw_data = {'시간': time_lst, '체결가': price_lst}
    #raw_data = {'체결가': price_lst}
    data = pd.DataFrame(raw_data)
    #data =pd.DataFrame(raw_data, index= time_lst)
    #print(data)
    return data

def aftertimeprice(n,data): #n분 후
    after_price_lst=[]
    for i in range(len(data)) :
        is_time=data['시간']==data.loc[i]['시간']+datetime.timedelta(minutes=n) #각 행에대해서 n분 후의 가격이 존재하면 리스트에 추가
        temp=data[is_time].reset_index(drop=True)
        if(temp.empty==False) :
            after_price_lst.append(temp.loc[0]['체결가'])
        else: #1분후 값이 존재하지 않는 부분 n분 5초후 or  nan으로 채움
            is_time = data['시간'] == data.loc[i]['시간'] + datetime.timedelta(minutes=n,seconds=5)
            temp = data[is_time].reset_index(drop=True)
            if (temp.empty == False):
                after_price_lst.append(temp.loc[0]['체결가'])
            else: #그래도 비었을 경우 nan값
                after_price_lst.append(np.nan)
    #print(len(after_price_lst))
    line=str(n)+"분후"
    data[line]=after_price_lst #n분후 가격 저장한 열추가

    for i in range(len(data)):
        if (data.loc[i][line] != np.nan):
            rate = data.loc[i][line] / data.loc[i]['체결가']
        else:
            rate = np.nan
        rate_lst.append(rate)
    print(len(rate_lst))
    data['상승률'] = rate_lst
    return data

data=func1()
data=aftertimeprice(1,data)
data=data.fillna('missing')


data1=data
data1.index = data.시간
del data1['시간']
#data1=pd.DataFrame(data.체결가, index=data.시간)
print(data1)
df=pd.DataFrame()
df['상승률'] =data1.상승률.resample('1T').first()

print(df)

#excel 파일로 작성
"""base_dir="C:/Users/82107/PycharmProjects/DartProject"
file_nm="data.xlsx"
file_nm2="label.xlsx"
xlsx_dir=os.path.join(base_dir,file_nm)
data.to_excel(xlsx_dir)
xlsx_dir=os.path.join(base_dir,file_nm2)
data['상승률'].to_excel(xlsx_dir)"""

In [ ]:
#import packages
"""...
"""

import numpy as np
import pandas as pd
from keras import Sequential
from keras.models import load_model
from keras.layers import Dense, Activation, LSTM
import time

In [ ]:
#HyperParameters

input_dim = 2 #입력하는 feature 개수
time_interval = 8 #minute. n분 마다 n분 누적 신호 발생. 혹은 lstm cell에서 시계열의 갯수

n_cell = 32
n_labels = 4 #모델의 결과 값 라벨 수 e.g. n=4, 라벨이 강하락, 약하락, 약상승, 강상승 신호 발생.
seq_length = 14 # 모델이 참고 할 이전 분봉의 개수. LSTM/RNN에서
lr = 0.003 # learning rate
keep_prob = 1.0 #dropout rate
n_stacked_layer = 1 # 모델의 레이어 개수
n_epochs = 1000 # 학습횟수. 얼리스타핑 넣을까말까
n_batch_size = 32


In [ ]:
import win32com.client
from PyQt5.QtCore import pyqtSignal, QObject
class CreonAPI(QObject):
    receive_real_stockcur_signal = pyqtSignal(tuple)
    
    @classmethod
    def get_instance(cls):
        cp_cur = win32com.client.DispatchWithEvents("dscbo1.StockCur", cls)
        return cp_cur
    
    def get_real(self, stockcode="005930"):
        creon_stockcode = 'A' + stockcode  # 대신은 주식 종목코드가 'A'로 시작해야함.
        self.SetInputValue(0, creon_stockcode)  # 0 - (string) 종목 코드
        self.Subscribe()

    def stop_real(self, stockcode: str):
        creon_stockcode = 'A' + stockcode  # 대신은 주식 종목코드가 'A'로 시작해야함.
        self.SetInputValue(0, creon_stockcode)  # 0 - (string) 종목 코드
        self.Unsubscribe()
        
    def OnReceived(self):
        code = self.GetHeaderValue(0)  # 0 - (string) 종목코드
        stockcode = code[1:]  # 'A' 제외시킴.
        ttime = self.GetHeaderValue(18)  # 18 - (long) 시간 (초)
        sell_price = self.GetHeaderValue(7)  # 7 - (long) 매도호가
        buy_price = self.GetHeaderValue(8)  # 8 - (long) 매수호가
        price = self.GetHeaderValue(13)  # 13 - (long) 현재가 또는 예상체결가 ( 19번 예상체결가 구분 플래그에 따라 달라짐)
        predict_price = chr(self.GetHeaderValue(19))  # 19 - (char)예상체결가 구분플래그 ; '1' -> 동시호가시간(예상체결가), '2' -> 장중 (체결)

        state = chr(self.GetHeaderValue(14))  # 14 - (char)체결상태 ; '1' -> 매수, '2' -> 매도
        vol = self.GetHeaderValue(9)  # 9 - (long) 누적거래량  [주의] 기준단위를확인하세요
        vol2 = self.GetHeaderValue(17)  # 17 - (long) 순간체결수량
        money = self.GetHeaderValue(10)  # 10 - (long) 누적거래대금[주의] 기준단위를확인하세요

        pos = chr(self.GetHeaderValue(26))  # 26 - (char)체결상태 (호가방식) - 1.매수/ 2.매도
        vol_sell = self.GetHeaderValue(27)  # 27 - (long) 누적매도체결수량 (호가방식)
        vol_buy = self.GetHeaderValue(28)  # 28 - (long) 누적매수체결수량 (호가방식)
        jang = chr(self.GetHeaderValue(20))  # 20 - (char)장구분플래그;  '2'->장중, '2'->장후시간외 '5'->장후예상체결

        diff = self.GetHeaderValue(2)  # 전일대비
        op = self.GetHeaderValue(4)  # 시가
        hi = self.GetHeaderValue(5)  # 고가
        lo = self.GetHeaderValue(6)  # 저가

        if pos == '1':
            hoga_sign = '+'
        else:
            hoga_sign = '-'

        tick = (stockcode, ttime, sell_price, buy_price, price, state, pos, hoga_sign, vol2, vol, vol_sell, vol_buy, money, jang)
        self.receive_real_stockcur_signal.emit(tick)
        # print("---- self.receive_real_stockcur_signal.emit---")    
api = CreonAPI.get_instance()
#api.receive_real_stockcur_signal.connect(self.__receive_real_stockcur)
api.get_real('005930')
api.OnReceived() # ???

In [ ]:
# DataLoading on API
# API에서 필요한 데이터를 가져오는 부분.
# 모델 학습 및 테스팅 데이터 가져오는 부분과
# 트레이딩 알고리즘에 실시간으로 전송할 데이터를 가져오는 함수 두 가지 필요
class DataReciever:
    def __init__(self, stockCode, buffer):
        self.api = CreonAPI.get_instance()
        self.stockCode = stockCode
        self.buffer = buffer#??? 버퍼와 데이터리시버는 상호참조? 혹은 리시버 has 버퍼
    
    #데이터를 불러옴
    def loadData(self):
        pass
    
    #데이터를 저장(훈련용)
    def saveData(self):
        pass
    
    # 데이터 발생 시 마다 버퍼가 데이터를 자동으로 받음.
    def emitData(self):

In [ ]:
# Data Preprocessing for Trainng
# API에서 받아온 대용량 데이터를 모델 학습을 위해 인풋과 라벨값이 있는 지도학습 데이터로 바꿔주는 부분

In [ ]:
# Data Preprocessing for predicting
# 실제 트레이딩 시, API에서 받아온 실시간 데이터를 버퍼에 넣기 전까지 전처리 하는 과정

In [ ]:
# Data Buffer
# API에서 받아온 데이터가 전처리 되어 저장되는 공간.
# n분마다 누적 데이터가 모델에 전송되며 버퍼를 초기화 함.
class DataBuffer:
    def __init__(self, dataReciever, model):
        self.dataStream = dataStream
        self.model = model
    
    #Queue를 만들고 Queue가 갱신(새 데이터가 들어옴)될 때 마다 모델에 데이터 전송

In [ ]:
# Data Seperating ( Training / Validating / Testing)
# 학습용 데이터 전처리 과정에서 받아온 데이터를 트레이닝 밸리데이팅 테스팅 데이터로 나누는 부분

from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split(preprocessed_Data, preprocessed_Data['Label'], test_size = 0.3, random_state=13)


In [ ]:
# Model Training & Saving
# 모델 생성 및 학습. 결과 저장

from keras import metrics

model = Sequential()
model.add(LSTM(n_cell, input_shape=(time_interval, input_dim), activation='sigmoid'))
model.add(Dense(4, activation='softmax'))

model.compile(loss='mse', optimizer='adam', metrics=[metrics.categorical_accuracy])
#무슨 loss func, optimizer를 써야할지, 메트릭스를 써야할지 모르겠다. 일단 보류.

history = model.fit(x = x_train, y = y_train, batch_size=n_batch_size, epochs = n_epochs, validation_split=0.3)
#밸리데이션 세퍼레잇 햇음. 데이터를 트레인 테스트로 8:2로 나눈다음 8을 5.6 : 2.4로 트레인 : 밸릳 데이터로 나눔.

plt.plot(history.losses)
plt.ylabel('loss')
plt.xlabel('epoch')
plt.legend(['train'], loc='upper left')
plt.show()

#model.evaluate()
#model.save()

In [ ]:
# Model Testing(생략가능)
# 테스팅 데이터로 모델 테스트.
# 목표 Loss 값이 될 때 까지 전 단계(생성/학습) 반복
# 한 칸 위 코드를 모듈화해서 하이퍼파라미터 변경 후 최고 점수 모델 저장.

In [ ]:
# Trading with Trained Model
# 모델이 데이터버퍼에서 데이터를 받고 받은 데이터를 통해 신호 발생 및 API에 매매 구현.

In [ ]:
# Logging
# 트레이딩 결과 추적 및 기초통계량 작성

In [ ]:
# System Trading w/ Model(MAIN LOOP)

datareciever = DataReciever() # API에서 데이터 리시버
buffer = DataBuffer() # 데이터 버퍼
model = model.load()
algorithm / or transactioner = asafsfdaf()
Logger

In [1]:
# single processing
import time
start_time = time.time()

def count(name):
    for i in range(1, 50001):
        print(f"{name} : {i}")

proc_list = ['p1' , 'p2' ,'p3', 'p4']
for num in proc_list:
    count(num)

print(f"------{time.time() - start_time} seconds passed")

p1 : 1
p1 : 2
p1 : 3
p1 : 4
p1 : 5
p1 : 6
p1 : 7
p1 : 8
p1 : 9
p1 : 10
p1 : 11
p1 : 12
p1 : 13
p1 : 14
p1 : 15
p1 : 16
p1 : 17
p1 : 18
p1 : 19
p1 : 20
p1 : 21
p1 : 22
p1 : 23
p1 : 24
p1 : 25
p1 : 26
p1 : 27
p1 : 28
p1 : 29
p1 : 30
p1 : 31
p1 : 32
p1 : 33
p1 : 34
p1 : 35
p1 : 36
p1 : 37
p1 : 38
p1 : 39
p1 : 40
p1 : 41
p1 : 42
p1 : 43
p1 : 44
p1 : 45
p1 : 46
p1 : 47
p1 : 48
p1 : 49
p1 : 50
p1 : 51
p1 : 52
p1 : 53
p1 : 54
p1 : 55
p1 : 56
p1 : 57
p1 : 58
p1 : 59
p1 : 60
p1 : 61
p1 : 62
p1 : 63
p1 : 64
p1 : 65
p1 : 66
p1 : 67
p1 : 68
p1 : 69
p1 : 70
p1 : 71
p1 : 72
p1 : 73
p1 : 74
p1 : 75
p1 : 76
p1 : 77
p1 : 78
p1 : 79
p1 : 80
p1 : 81
p1 : 82
p1 : 83
p1 : 84
p1 : 85
p1 : 86
p1 : 87
p1 : 88
p1 : 89
p1 : 90
p1 : 91
p1 : 92
p1 : 93
p1 : 94
p1 : 95
p1 : 96
p1 : 97
p1 : 98
p1 : 99
p1 : 100
p1 : 101
p1 : 102
p1 : 103
p1 : 104
p1 : 105
p1 : 106
p1 : 107
p1 : 108
p1 : 109
p1 : 110
p1 : 111
p1 : 112
p1 : 113
p1 : 114
p1 : 115
p1 : 116
p1 : 117
p1 : 118
p1 : 119
p1 : 120
p1 : 121
p1 : 122
p1 : 123
p

p1 : 2986
p1 : 2987
p1 : 2988
p1 : 2989
p1 : 2990
p1 : 2991
p1 : 2992
p1 : 2993
p1 : 2994
p1 : 2995
p1 : 2996
p1 : 2997
p1 : 2998
p1 : 2999
p1 : 3000
p1 : 3001
p1 : 3002
p1 : 3003
p1 : 3004
p1 : 3005
p1 : 3006
p1 : 3007
p1 : 3008
p1 : 3009
p1 : 3010
p1 : 3011
p1 : 3012
p1 : 3013
p1 : 3014
p1 : 3015
p1 : 3016
p1 : 3017
p1 : 3018
p1 : 3019
p1 : 3020
p1 : 3021
p1 : 3022
p1 : 3023
p1 : 3024
p1 : 3025
p1 : 3026
p1 : 3027
p1 : 3028
p1 : 3029
p1 : 3030
p1 : 3031
p1 : 3032
p1 : 3033
p1 : 3034
p1 : 3035
p1 : 3036
p1 : 3037
p1 : 3038
p1 : 3039
p1 : 3040
p1 : 3041
p1 : 3042
p1 : 3043
p1 : 3044
p1 : 3045
p1 : 3046
p1 : 3047
p1 : 3048
p1 : 3049
p1 : 3050
p1 : 3051
p1 : 3052
p1 : 3053
p1 : 3054
p1 : 3055
p1 : 3056
p1 : 3057
p1 : 3058
p1 : 3059
p1 : 3060
p1 : 3061
p1 : 3062
p1 : 3063
p1 : 3064
p1 : 3065
p1 : 3066
p1 : 3067
p1 : 3068
p1 : 3069
p1 : 3070
p1 : 3071
p1 : 3072
p1 : 3073
p1 : 3074
p1 : 3075
p1 : 3076
p1 : 3077
p1 : 3078
p1 : 3079
p1 : 3080
p1 : 3081
p1 : 3082
p1 : 3083
p1 : 3084
p1 : 3085


p1 : 5964
p1 : 5965
p1 : 5966
p1 : 5967
p1 : 5968
p1 : 5969
p1 : 5970
p1 : 5971
p1 : 5972
p1 : 5973
p1 : 5974
p1 : 5975
p1 : 5976
p1 : 5977
p1 : 5978
p1 : 5979
p1 : 5980
p1 : 5981
p1 : 5982
p1 : 5983
p1 : 5984
p1 : 5985
p1 : 5986
p1 : 5987
p1 : 5988
p1 : 5989
p1 : 5990
p1 : 5991
p1 : 5992
p1 : 5993
p1 : 5994
p1 : 5995
p1 : 5996
p1 : 5997
p1 : 5998
p1 : 5999
p1 : 6000
p1 : 6001
p1 : 6002
p1 : 6003
p1 : 6004
p1 : 6005
p1 : 6006
p1 : 6007
p1 : 6008
p1 : 6009
p1 : 6010
p1 : 6011
p1 : 6012
p1 : 6013
p1 : 6014
p1 : 6015
p1 : 6016
p1 : 6017
p1 : 6018
p1 : 6019
p1 : 6020
p1 : 6021
p1 : 6022
p1 : 6023
p1 : 6024
p1 : 6025
p1 : 6026
p1 : 6027
p1 : 6028
p1 : 6029
p1 : 6030
p1 : 6031
p1 : 6032
p1 : 6033
p1 : 6034
p1 : 6035
p1 : 6036
p1 : 6037
p1 : 6038
p1 : 6039
p1 : 6040
p1 : 6041
p1 : 6042
p1 : 6043
p1 : 6044
p1 : 6045
p1 : 6046
p1 : 6047
p1 : 6048
p1 : 6049
p1 : 6050
p1 : 6051
p1 : 6052
p1 : 6053
p1 : 6054
p1 : 6055
p1 : 6056
p1 : 6057
p1 : 6058
p1 : 6059
p1 : 6060
p1 : 6061
p1 : 6062
p1 : 6063


p1 : 8836
p1 : 8837
p1 : 8838
p1 : 8839
p1 : 8840
p1 : 8841
p1 : 8842
p1 : 8843
p1 : 8844
p1 : 8845
p1 : 8846
p1 : 8847
p1 : 8848
p1 : 8849
p1 : 8850
p1 : 8851
p1 : 8852
p1 : 8853
p1 : 8854
p1 : 8855
p1 : 8856
p1 : 8857
p1 : 8858
p1 : 8859
p1 : 8860
p1 : 8861
p1 : 8862
p1 : 8863
p1 : 8864
p1 : 8865
p1 : 8866
p1 : 8867
p1 : 8868
p1 : 8869
p1 : 8870
p1 : 8871
p1 : 8872
p1 : 8873
p1 : 8874
p1 : 8875
p1 : 8876
p1 : 8877
p1 : 8878
p1 : 8879
p1 : 8880
p1 : 8881
p1 : 8882
p1 : 8883
p1 : 8884
p1 : 8885
p1 : 8886
p1 : 8887
p1 : 8888
p1 : 8889
p1 : 8890
p1 : 8891
p1 : 8892
p1 : 8893
p1 : 8894
p1 : 8895
p1 : 8896
p1 : 8897
p1 : 8898
p1 : 8899
p1 : 8900
p1 : 8901
p1 : 8902
p1 : 8903
p1 : 8904
p1 : 8905
p1 : 8906
p1 : 8907
p1 : 8908
p1 : 8909
p1 : 8910
p1 : 8911
p1 : 8912
p1 : 8913
p1 : 8914
p1 : 8915
p1 : 8916
p1 : 8917
p1 : 8918
p1 : 8919
p1 : 8920
p1 : 8921
p1 : 8922
p1 : 8923
p1 : 8924
p1 : 8925
p1 : 8926
p1 : 8927
p1 : 8928
p1 : 8929
p1 : 8930
p1 : 8931
p1 : 8932
p1 : 8933
p1 : 8934
p1 : 8935


p1 : 11803
p1 : 11804
p1 : 11805
p1 : 11806
p1 : 11807
p1 : 11808
p1 : 11809
p1 : 11810
p1 : 11811
p1 : 11812
p1 : 11813
p1 : 11814
p1 : 11815
p1 : 11816
p1 : 11817
p1 : 11818
p1 : 11819
p1 : 11820
p1 : 11821
p1 : 11822
p1 : 11823
p1 : 11824
p1 : 11825
p1 : 11826
p1 : 11827
p1 : 11828
p1 : 11829
p1 : 11830
p1 : 11831
p1 : 11832
p1 : 11833
p1 : 11834
p1 : 11835
p1 : 11836
p1 : 11837
p1 : 11838
p1 : 11839
p1 : 11840
p1 : 11841
p1 : 11842
p1 : 11843
p1 : 11844
p1 : 11845
p1 : 11846
p1 : 11847
p1 : 11848
p1 : 11849
p1 : 11850
p1 : 11851
p1 : 11852
p1 : 11853
p1 : 11854
p1 : 11855
p1 : 11856
p1 : 11857
p1 : 11858
p1 : 11859
p1 : 11860
p1 : 11861
p1 : 11862
p1 : 11863
p1 : 11864
p1 : 11865
p1 : 11866
p1 : 11867
p1 : 11868
p1 : 11869
p1 : 11870
p1 : 11871
p1 : 11872
p1 : 11873
p1 : 11874
p1 : 11875
p1 : 11876
p1 : 11877
p1 : 11878
p1 : 11879
p1 : 11880
p1 : 11881
p1 : 11882
p1 : 11883
p1 : 11884
p1 : 11885
p1 : 11886
p1 : 11887
p1 : 11888
p1 : 11889
p1 : 11890
p1 : 11891
p1 : 11892
p1 : 11893

...

p4 : 34457
p4 : 34458
p4 : 34459
p4 : 34460
p4 : 34461
p4 : 34462
p4 : 34463
p4 : 34464
p4 : 34465
p4 : 34466
p4 : 34467
p4 : 34468
p4 : 34469
p4 : 34470
p4 : 34471
p4 : 34472
p4 : 34473
p4 : 34474
p4 : 34475
p4 : 34476
p4 : 34477
p4 : 34478
p4 : 34479
p4 : 34480
p4 : 34481
p4 : 34482
p4 : 34483
p4 : 34484
p4 : 34485
p4 : 34486
p4 : 34487
p4 : 34488
p4 : 34489
p4 : 34490
p4 : 34491
p4 : 34492
p4 : 34493
p4 : 34494
p4 : 34495
p4 : 34496
p4 : 34497
p4 : 34498
p4 : 34499
p4 : 34500
p4 : 34501
p4 : 34502
p4 : 34503
p4 : 34504
p4 : 34505
p4 : 34506
p4 : 34507
p4 : 34508
p4 : 34509
p4 : 34510
p4 : 34511
p4 : 34512
p4 : 34513
p4 : 34514
p4 : 34515
p4 : 34516
p4 : 34517
p4 : 34518
p4 : 34519
p4 : 34520
p4 : 34521
p4 : 34522
p4 : 34523
p4 : 34524
p4 : 34525
p4 : 34526
p4 : 34527
p4 : 34528
p4 : 34529
p4 : 34530
p4 : 34531
p4 : 34532
p4 : 34533
p4 : 34534
p4 : 34535
p4 : 34536
p4 : 34537
p4 : 34538
p4 : 34539
p4 : 34540
p4 : 34541
p4 : 34542
p4 : 34543
p4 : 34544
p4 : 34545
p4 : 34546
p4 : 34547

p4 : 37957
p4 : 37958
p4 : 37959
p4 : 37960
p4 : 37961
p4 : 37962
p4 : 37963
p4 : 37964
p4 : 37965
p4 : 37966
p4 : 37967
p4 : 37968
p4 : 37969
p4 : 37970
p4 : 37971
p4 : 37972
p4 : 37973
p4 : 37974
p4 : 37975
p4 : 37976
p4 : 37977
p4 : 37978
p4 : 37979
p4 : 37980
p4 : 37981
p4 : 37982
p4 : 37983
p4 : 37984
p4 : 37985
p4 : 37986
p4 : 37987
p4 : 37988
p4 : 37989
p4 : 37990
p4 : 37991
p4 : 37992
p4 : 37993
p4 : 37994
p4 : 37995
p4 : 37996
p4 : 37997
p4 : 37998
p4 : 37999
p4 : 38000
p4 : 38001
p4 : 38002
p4 : 38003
p4 : 38004
p4 : 38005
p4 : 38006
p4 : 38007
p4 : 38008
p4 : 38009
p4 : 38010
p4 : 38011
p4 : 38012
p4 : 38013
p4 : 38014
p4 : 38015
p4 : 38016
p4 : 38017
p4 : 38018
p4 : 38019
p4 : 38020
p4 : 38021
p4 : 38022
p4 : 38023
p4 : 38024
p4 : 38025
p4 : 38026
p4 : 38027
p4 : 38028
p4 : 38029
p4 : 38030
p4 : 38031
p4 : 38032
p4 : 38033
p4 : 38034
p4 : 38035
p4 : 38036
p4 : 38037
p4 : 38038
p4 : 38039
p4 : 38040
p4 : 38041
p4 : 38042
p4 : 38043
p4 : 38044
p4 : 38045
p4 : 38046
p4 : 38047

p4 : 41407
p4 : 41408
p4 : 41409
p4 : 41410
p4 : 41411
p4 : 41412
p4 : 41413
p4 : 41414
p4 : 41415
p4 : 41416
p4 : 41417
p4 : 41418
p4 : 41419
p4 : 41420
p4 : 41421
p4 : 41422
p4 : 41423
p4 : 41424
p4 : 41425
p4 : 41426
p4 : 41427
p4 : 41428
p4 : 41429
p4 : 41430
p4 : 41431
p4 : 41432
p4 : 41433
p4 : 41434
p4 : 41435
p4 : 41436
p4 : 41437
p4 : 41438
p4 : 41439
p4 : 41440
p4 : 41441
p4 : 41442
p4 : 41443
p4 : 41444
p4 : 41445
p4 : 41446
p4 : 41447
p4 : 41448
p4 : 41449
p4 : 41450
p4 : 41451
p4 : 41452
p4 : 41453
p4 : 41454
p4 : 41455
p4 : 41456
p4 : 41457
p4 : 41458
p4 : 41459
p4 : 41460
p4 : 41461
p4 : 41462
p4 : 41463
p4 : 41464
p4 : 41465
p4 : 41466
p4 : 41467
p4 : 41468
p4 : 41469
p4 : 41470
p4 : 41471
p4 : 41472
p4 : 41473
p4 : 41474
p4 : 41475
p4 : 41476
p4 : 41477
p4 : 41478
p4 : 41479
p4 : 41480
p4 : 41481
p4 : 41482
p4 : 41483
p4 : 41484
p4 : 41485
p4 : 41486
p4 : 41487
p4 : 41488
p4 : 41489
p4 : 41490
p4 : 41491
p4 : 41492
p4 : 41493
p4 : 41494
p4 : 41495
p4 : 41496
p4 : 41497

p4 : 44456
p4 : 44457
p4 : 44458
p4 : 44459
p4 : 44460
p4 : 44461
p4 : 44462
p4 : 44463
p4 : 44464
p4 : 44465
p4 : 44466
p4 : 44467
p4 : 44468
p4 : 44469
p4 : 44470
p4 : 44471
p4 : 44472
p4 : 44473
p4 : 44474
p4 : 44475
p4 : 44476
p4 : 44477
p4 : 44478
p4 : 44479
p4 : 44480
p4 : 44481
p4 : 44482
p4 : 44483
p4 : 44484
p4 : 44485
p4 : 44486
p4 : 44487
p4 : 44488
p4 : 44489
p4 : 44490
p4 : 44491
p4 : 44492
p4 : 44493
p4 : 44494
p4 : 44495
p4 : 44496
p4 : 44497
p4 : 44498
p4 : 44499
p4 : 44500
p4 : 44501
p4 : 44502
p4 : 44503
p4 : 44504
p4 : 44505
p4 : 44506
p4 : 44507
p4 : 44508
p4 : 44509
p4 : 44510
p4 : 44511
p4 : 44512
p4 : 44513
p4 : 44514
p4 : 44515
p4 : 44516
p4 : 44517
p4 : 44518
p4 : 44519
p4 : 44520
p4 : 44521
p4 : 44522
p4 : 44523
p4 : 44524
p4 : 44525
p4 : 44526
p4 : 44527
p4 : 44528
p4 : 44529
p4 : 44530
p4 : 44531
p4 : 44532
p4 : 44533
p4 : 44534
p4 : 44535
p4 : 44536
p4 : 44537
p4 : 44538
p4 : 44539
p4 : 44540
p4 : 44541
p4 : 44542
p4 : 44543
p4 : 44544
p4 : 44545
p4 : 44546

p4 : 47744
p4 : 47745
p4 : 47746
p4 : 47747
p4 : 47748
p4 : 47749
p4 : 47750
p4 : 47751
p4 : 47752
p4 : 47753
p4 : 47754
p4 : 47755
p4 : 47756
p4 : 47757
p4 : 47758
p4 : 47759
p4 : 47760
p4 : 47761
p4 : 47762
p4 : 47763
p4 : 47764
p4 : 47765
p4 : 47766
p4 : 47767
p4 : 47768
p4 : 47769
p4 : 47770
p4 : 47771
p4 : 47772
p4 : 47773
p4 : 47774
p4 : 47775
p4 : 47776
p4 : 47777
p4 : 47778
p4 : 47779
p4 : 47780
p4 : 47781
p4 : 47782
p4 : 47783
p4 : 47784
p4 : 47785
p4 : 47786
p4 : 47787
p4 : 47788
p4 : 47789
p4 : 47790
p4 : 47791
p4 : 47792
p4 : 47793
p4 : 47794
p4 : 47795
p4 : 47796
p4 : 47797
p4 : 47798
p4 : 47799
p4 : 47800
p4 : 47801
p4 : 47802
p4 : 47803
p4 : 47804
p4 : 47805
p4 : 47806
p4 : 47807
p4 : 47808
p4 : 47809
p4 : 47810
p4 : 47811
p4 : 47812
p4 : 47813
p4 : 47814
p4 : 47815
p4 : 47816
p4 : 47817
p4 : 47818
p4 : 47819
p4 : 47820
p4 : 47821
p4 : 47822
p4 : 47823
p4 : 47824
p4 : 47825
p4 : 47826
p4 : 47827
p4 : 47828
p4 : 47829
p4 : 47830
p4 : 47831
p4 : 47832
p4 : 47833
p4 : 47834

In [ ]:
# multi processing

import multiprocessing
import time
proc_list = ['p1' , 'p2' ,'p3', 'p4']

def count(name):
    for i in range(1,501):
        print(name, " : ", i)
if __name__ == '__main__':
    pool = multiprocessing.Pool(processes=4)
    pool.map(count, proc_list)
    pool.close()
    pool.join()
